In [1]:
!pip install haversine

In [2]:
import pandas as pd
import numpy as np
import pickle
from sklearn.metrics import f1_score
from sklearn.model_selection import train_test_split
from haversine import haversine
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score
#from mdlp.discretization import MDLP

In [3]:
bookings_original = pd.read_csv("data/raw/booking_log.csv")
participants_original = pd.read_csv("data/raw/participant_log.csv")
test = pd.read_csv("data/raw/test_data.csv")

In [4]:
test.shape

(100000, 10)

# EDA

In [5]:
bookings_original.head(5),bookings_original.shape

(                  event_timestamp      order_id booking_status   customer_id  \
 0     2015-05-12 05:25:23.904 UTC  102254181112        CREATED  715281995014   
 1      2015-05-12 05:25:24.67 UTC  102254181112   DRIVER_FOUND  715281995014   
 2  2015-05-12 05:55:10.496544 UTC  102254181112      COMPLETED  715281995014   
 3     2015-05-12 05:29:37.305 UTC  105520285203        CREATED  957980952237   
 4     2015-05-12 05:29:38.214 UTC  105520285203   DRIVER_FOUND  957980952237   
 
       driver_id  trip_distance  pickup_latitude  pickup_longitude  
 0           NaN            2.0        -2.998461        104.788077  
 1  2.211727e+11            2.0        -2.998461        104.788077  
 2  2.211727e+11            2.0        -2.998461        104.788077  
 3           NaN            2.0        -2.970621        104.756226  
 4  5.276724e+11            2.0        -2.970621        104.756226  ,
 (699212, 8))

In [6]:
bookings = bookings_original.drop(['event_timestamp','booking_status','driver_id'],axis=1)

In [7]:
unique_columns = [
        "order_id",
        "trip_distance",
        "pickup_latitude",
        "pickup_longitude",
    ]
bookings = bookings.drop_duplicates(subset=unique_columns)

In [8]:
participants = participants_original.drop_duplicates()
participants.head(5),participants.shape

(               event_timestamp     driver_id participant_status      order_id  \
 0  2015-05-18 11:45:19.519 UTC  110283102582            CREATED  938125906616   
 1    2015-05-18 11:45:29.8 UTC  110283102582           ACCEPTED  938125906616   
 2  2015-05-11 10:35:57.021 UTC  126346998414            CREATED  992080359113   
 3  2015-05-11 10:36:01.148 UTC  126346998414           ACCEPTED  992080359113   
 4  2015-05-16 12:34:20.044 UTC  199325048812           ACCEPTED  797723880713   
 
    experiment_key  driver_latitude  driver_longitude  driver_gps_accuracy  
 0    309579604593        -2.981389        104.761898                  2.0  
 1    309579604593        -2.981389        104.761898                  2.0  
 2    941995970460        -2.966915        104.748040                  2.0  
 3    941995970460        -2.966915        104.748040                  2.0  
 4    197604093364        -3.014740        104.694647                  2.0  ,
 (400104, 8))

In [9]:
test.head(5),test.shape

(               event_timestamp      order_id   customer_id  trip_distance  \
 0  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 1  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 2  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 3  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 4  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 
    pickup_latitude  pickup_longitude     driver_id  driver_latitude  \
 0        -2.977965         104.77559  578486386000        -2.979892   
 1        -2.977965         104.77559  919898718450        -2.979352   
 2        -2.977965         104.77559  566354734208        -2.978990   
 3        -2.977965         104.77559  996326998494        -2.979434   
 4        -2.977965         104.77559  110774820109        -2.979365   
 
    driver_longitude  driver_gps_accuracy  
 0        104.775853              104.100  
 1      

In [10]:
dataset = pd.merge(participants,bookings, on = "order_id", how="left")

In [11]:
#19May 2015 is missing in participants_log but is present in bookings_log, bcoz merge is done on participants, dataset does not have this date
dataset.event_timestamp.min(),dataset.event_timestamp.max(),test.event_timestamp.min(),test.event_timestamp.max(),participants.event_timestamp.max()

('2015-05-10 00:00:11.845 UTC',
 '2015-05-18 23:59:59.632 UTC',
 '2015-05-20 00:00:18.427 UTC',
 '2015-05-20 23:59:58.789 UTC',
 '2015-05-18 23:59:59.632 UTC')

In [12]:
dataset.drop(['experiment_key'],inplace=True,axis=1)
dataset.shape

(400104, 11)

In [13]:
#This shows that maximum 174/2 requests lie with 1 driver in this dataset as largely each driver with request will have 2 entries,
# one at time of creation and other at time of response
dataset.driver_id.value_counts()

621987433025    174
622447347300    172
271936096806    166
178632046874    163
766627766512    163
               ... 
902095281838      1
917939363137      1
732388817640      1
709961499772      1
204107384010      1
Name: driver_id, Length: 14913, dtype: int64

In [14]:
dataset.head(5)

event_timestamp     driver_id participant_status      order_id  \
0  2015-05-18 11:45:19.519 UTC  110283102582            CREATED  938125906616   
1    2015-05-18 11:45:29.8 UTC  110283102582           ACCEPTED  938125906616   
2  2015-05-11 10:35:57.021 UTC  126346998414            CREATED  992080359113   
3  2015-05-11 10:36:01.148 UTC  126346998414           ACCEPTED  992080359113   
4  2015-05-16 12:34:20.044 UTC  199325048812           ACCEPTED  797723880713   

   driver_latitude  driver_longitude  driver_gps_accuracy   customer_id  \
0        -2.981389        104.761898                  2.0  786955815516   
1        -2.981389        104.761898                  2.0  786955815516   
2        -2.966915        104.748040                  2.0  758692050609   
3        -2.966915        104.748040                  2.0  758692050609   
4        -3.014740        104.694647                  2.0  967731380169   

   trip_distance  pickup_latitude  pickup_longitude  
0          5.601        -2.980337        104.761200  
1          5.601        -2.980337        104.761200  
2          1.744        -2.968359        104.749344  
3          1.744        -2.968359        104.749344  
4          2.505        -3.013223        104.700030

In [15]:
#This code finds those order_ID and driver_id pairs for which only CREATED status row is present and there is no info about driver's response.
#Also it helps us to know if this behaviour is driver dependent. .
dataset.groupby(["order_id","driver_id"]).filter(lambda x: len(x)==1)["driver_id"].value_counts()

705573313466    7
457765057674    4
238210291329    4
381538151896    4
174566916689    4
               ..
189731800340    1
368151360724    1
699542607016    1
347825505488    1
475534069815    1
Name: driver_id, Length: 1000, dtype: int64

In [16]:
#This checks how many requests did the above driver "705573313466" got in order to know the ratio of rides for which info is
#absent and 43/2 i.e out od 21 rides information for 7 rides is missing. Info below shows that maybe this driver is faulty or  
#Maybe that data is missing and hence we can remove those rows
dataset["driver_id"].value_counts()[705573313466]

43

In [17]:
#Creating a column called "driver response time" by subtracting the timestamp in the two rows with 
#respective CREATED and "ACCEPTED/REJECTED/IGNORED" value.
dataset_featured = dataset.groupby(["order_id","driver_id"]).filter(lambda x: len(x)>1)

# Feature Engineering

In [18]:
def response_time(order):
    order = pd.DataFrame(order)
    if order.iloc[0]["participant_status"] == "CREATED":
        order["driver_response_time"] = (order.iloc[1]["event_timestamp"] - order.iloc[0]["event_timestamp"]).total_seconds()
        print(type(order.iloc[0]["driver_response_time"]))
    else:
        order["driver_response_time"] = (order.iloc[0]["event_timestamp"] - order.iloc[1]["event_timestamp"]).total_seconds()
    return order

In [19]:
def get_cartesian(lat=None,lon=None):
    lat, lon = np.deg2rad(lat), np.deg2rad(lon)
    R = 6371 # radius of the earth
    x = R * np.cos(lat) * np.cos(lon)
    y = R * np.cos(lat) * np.sin(lon)
    z = R *np.sin(lat)
    return [x,y,z]

In [20]:
# #Find best K using elbow method. Result : K=25
# K = range(5, 50)
# inertias = [] 
# for k in K:
#     kmeanModel = KMeans(n_clusters=k).fit(df_cord_driver_cartesian)
#     inertias.append(kmeanModel.inertia_)

In [21]:
#If we were given personal info about the driver we could have had more feature columns describing the driver
def transform_train_val_test(df,train_or_test):
    df["event_timestamp"]=df["event_timestamp"].apply(lambda x: pd.to_datetime(x))
    #print(df["event_timestamp"])
    #df["date"] = df.event_timestamp.dt.date
    df["dayofweek"] = df.event_timestamp.dt.dayofweek
    df["hourofday"] = df.event_timestamp.dt.hour
    if train_or_test in ["train","val"]:
        df['participant_status'] = df['participant_status'].astype(str)
        df = df.groupby(["order_id","driver_id"]).apply(response_time)
        df = df[~(df["participant_status"].str.contains("CREATED"))]#As this info has been captured in "driver_response_time"
        df["participant_status"] = df["participant_status"].apply(lambda x: 1 if x=="ACCEPTED" else 0)
        driver_wise_response_time = pd.DataFrame(df.groupby(["driver_id"])["driver_response_time"].mean())
        driver_wise_response_time.to_csv("driver_wise_response_time.csv")
    if train_or_test == "test":
        driver_wise_response_time= pd.read_csv("driver_wise_response_time.csv")
        df = pd.merge(df,driver_wise_response_time, on="driver_id",how="left").fillna(driver_wise_response_time["driver_response_time"].mean())
#         transformer = MDLP(continuous_features=[True])
#         df['hourly_bins'] = transformer.fit_transform(np.array(df['hourofday']).reshape(-1, 1), df['participant_status'])
#         pickle.dump(transformer, open('transformer.pkl', 'wb'))
#     transformer = pickle.load(open("transformer.pkl", 'rb'))   
#     df['hourly_bins'] = transformer.transform(np.array(df['hourofday']).reshape(-1, 1), df['participant_status'])
    #df.groupby("hourofday")['is_accepted'].mean().plot , Plot shows that busy hours are between 5 and 15.
    df["is_busy_hour"] = df["hourofday"].apply(lambda x:  1 if x>=5 and x<=15 else 0)
    df["driver_distance"] = df.apply(lambda r: haversine((r["driver_latitude"], r["driver_longitude"]),
                            (r["pickup_latitude"], r["pickup_longitude"])),axis=1)
    df_cord_driver_cartesian = pd.DataFrame(df[["driver_latitude", "driver_longitude"]].apply(lambda x: get_cartesian(x["driver_latitude"],x["driver_longitude"]),axis=1).tolist())
    df_cord_customer_cartesian = pd.DataFrame(df[["pickup_latitude", "pickup_longitude"]].apply(lambda x: get_cartesian(x["pickup_latitude"],x["pickup_longitude"]),axis=1).tolist())    
    if train_or_test == "train":
        kmeanModel = KMeans(n_clusters=25).fit(df_cord_driver_cartesian)
        with open("kmeanModel.pkl", "wb") as f:
            pickle.dump(kmeanModel, f)
    kmeanModel = pickle.load(open("kmeanModel.pkl", 'rb'))
    df["driver_cluster_label"]= kmeanModel.predict(df_cord_driver_cartesian).tolist()
    df["customer_cluster_label"]= kmeanModel.predict(df_cord_customer_cartesian).tolist()
    df.drop(["event_timestamp","driver_latitude", "driver_longitude","pickup_latitude", "pickup_longitude","hourofday"],inplace=True, axis=1)
    return df

In [22]:
#Divide data into train and val after sorting on time so that while training we do not have future ride info
dataset_featured = dataset_featured.sort_values(by='event_timestamp',ascending=True)
dataset_featured_train, dataset_featured_val = dataset_featured.head(int(len(dataset_featured)*(80/100))),dataset_featured.tail(int(len(dataset_featured)*(20/100)))

In [23]:
transformed_train_data = transform_train_val_test(dataset_featured_train,"train")
transformed_val_data = transform_train_val_test(dataset_featured_val.sort_values(by='order_id',ascending=True),"val")
transformed_test_data = transform_train_val_test(test,"test")

<ipython-input-21-ca30c9b03584>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["event_timestamp"]=df["event_timestamp"].apply(lambda x: pd.to_datetime(x))
<ipython-input-21-ca30c9b03584>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["dayofweek"] = df.event_timestamp.dt.dayofweek
<ipython-input-21-ca30c9b03584>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation:

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

...

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>


In [24]:
# transformed_train_data = transform_train_val_test(dataset_featured_train[:100],"train")
# transformed_val_data = transform_train_val_test(dataset_featured_val.sort_values(by='order_id',ascending=True)[:20],"val")
# transformed_test_data = transform_train_val_test(test[:30],"test")

In [25]:
transformed_train_data.columns,transformed_test_data.columns

(Index(['driver_id', 'participant_status', 'order_id', 'driver_gps_accuracy',
        'customer_id', 'trip_distance', 'dayofweek', 'driver_response_time',
        'is_busy_hour', 'driver_distance', 'driver_cluster_label',
        'customer_cluster_label'],
       dtype='object'),
 Index(['order_id', 'customer_id', 'trip_distance', 'driver_id',
        'driver_gps_accuracy', 'dayofweek', 'driver_response_time',
        'is_busy_hour', 'driver_distance', 'driver_cluster_label',
        'customer_cluster_label'],
       dtype='object'))

In [26]:
train_y = transformed_train_data["participant_status"]
train_x = transformed_train_data.drop(["participant_status","order_id","customer_id"],axis=1)
val_y = transformed_val_data["participant_status"]
val_x = transformed_val_data.drop(["participant_status","order_id","customer_id"],axis=1)
#test = transformed_test_data

In [27]:
transformed_train_data.to_csv("data/processed/train_data_mahima.csv")
#transformed_test_data.to_csv("data/processed/test_data_mahima.csv")

In [28]:
val_y.shape,val_x.shape

((39897,), (39897, 9))

In [29]:
train_x.columns

Index(['driver_id', 'driver_gps_accuracy', 'trip_distance', 'dayofweek',
       'driver_response_time', 'is_busy_hour', 'driver_distance',
       'driver_cluster_label', 'customer_cluster_label'],
      dtype='object')

In [30]:
val_x.columns

Index(['driver_id', 'driver_gps_accuracy', 'trip_distance', 'dayofweek',
       'driver_response_time', 'is_busy_hour', 'driver_distance',
       'driver_cluster_label', 'customer_cluster_label'],
      dtype='object')

In [31]:
train_y.value_counts()

1    144652
0     14936
Name: participant_status, dtype: int64

# Modelling

LR or SVM as we are dealing with 2 class problem. SVM works well with unstructured and semi-structured data like text and images while logistic regression works with already identified independent variables. 

In [32]:
#Apply Random Forest or any other model to predict the probability of "participant_status" i.e. 0 or 1 for different drivers given the same 
#order_id and then return the driver with the maximum probability of accepting the request

In [33]:
def convert_pred_to_0_1(group):
    df = pd.DataFrame(group)
    df.iloc[0]["Pred_y"]=1
    df.iloc[1:]["Pred_y"]=0
    return df

In [43]:
transformed_train_data["participant_status"].value_counts()

1    144652
0     14936
Name: participant_status, dtype: int64

In [34]:
transformed_val_data.shape,transformed_train_data.shape

((39897, 12), (159588, 12))

In [113]:
clf = LogisticRegression(random_state=0).fit(train_x, train_y)
val_pred_y = clf.predict(val_x)
val_pred_y_df = pd.DataFrame(val_pred_y,columns=["Pred_y"])
transformed_val_data["index"]=transformed_val_data.index
val_pred_y_df["index"]=val_pred_y_df.index
x = pd.merge(transformed_val_data,val_pred_y_df,on="index").drop_duplicates()
result1 = x.sort_values("Pred_y",ascending=False).groupby(["order_id"]).apply(convert_pred_to_0_1)
score_accuracy =accuracy_score(result1["participant_status"],result1["Pred_y"])
# metrics = {}
# metrics["f_score_class_1"]=f1_score(result1["participant_status"],result1["Pred_y"],pos_label=1)
# metrics["f_score_class_0"]=f1_score(result1["participant_status"],result1["Pred_y"],pos_label=0)

In [114]:
#This is calculated to see that I should not assign a ride to a wrong driver or a driver that is highly probable to cancel. Looking
#at the results we see that for 291/3984 rides, I assigned a wrong driver. While 15/3984 drivers I predicted as the ones who won't 
#accept the ride despite the fact that they actually did
result1=pd.DataFrame(result1)
print(result1.shape)
result1.loc[(result1["Pred_y"]==1.0) & (result1["participant_status"]==0.0)]

(3984, 14)


driver_id  participant_status      order_id  driver_gps_accuracy  \
2648  478513399669                   0  698334680912                  3.0   
2649  534790575670                   0  698348267817                  3.0   
2662  208509859971                   0  701149692604                  3.0   
2615  242212206723                   0  691562579518                  3.0   
2628  743619182876                   0  694409316009                  3.0   
...            ...                 ...           ...                  ...   
1255  461910476878                   0  392678154509                  3.0   
1266  297230294848                   0  395542912005                  3.0   
1354  621987433025                   0  415766890308                  3.0   
1361  300820451126                   0  416870345607                  3.0   
1320  240328430994                   0  408477209202                  3.0   

       customer_id  trip_distance  dayofweek  driver_response_time  \
2648  926656485336          3.199          6                15.017   
2649  694745371081         12.692          0                15.017   
2662  647532660075          3.683          6                15.017   
2615  646904699896          6.244          0                15.023   
2628  792751093158          2.155          6                15.025   
...            ...            ...        ...                   ...   
1255  562069276403          7.544          6                15.024   
1266  678619945473          4.805          6                15.027   
1354  572115712745         11.848          0                15.021   
1361  417192026380          8.765          0                15.017   
1320  685677124848          6.582          6                10.009   

      is_busy_hour  driver_distance  driver_cluster_label  \
2648             1         0.310166                    23   
2649             0         0.444842                    18   
2662             1         0.051811                    11   
2615             1         0.345174                    17   
2628             1         0.004064                    17   
...            ...              ...                   ...   
1255             1         0.481446                    23   
1266             0         0.799061                    23   
1354             0         0.285336                     5   
1361             1         0.099409                    14   
1320             1         0.245266                    24   

      customer_cluster_label  index  Pred_y  
2648                      23  20888       1  
2649                      18  24191       1  
2662                      11   5870       1  
2615                      17   7789       1  
2628                      17  36291       1  
...                      ...    ...     ...  
1255                      23  19876       1  
1266                      23  10559       1  
1354                       5  28943       1  
1361                      14  10737       1  
1320                      24   7533       1  

[291 rows x 14 columns]

In [139]:
def is_correct_driver_identified(x):
    x = pd.DataFrame(x)
    x["is_correct_driver_identified"] = 0
    for i in range(x.shape[0]):
        if ((x.iloc[i]["participant_status"] == 1.0) and (x.iloc[i]["Pred_y"] == 1.0)):
            x["is_correct_driver_identified"] = 1
    return x

In [140]:
result1 = result1.groupby(["order_id"]).apply(lambda x: is_correct_driver_identified(x))

In [141]:
#Recall (i.e. 92% of the time I was able to capture the right driver). Note that our model is giving 1 only to 1 driver that has got the maximum prediction probability and rest all drivers get 0 
#while in practise for the same order ID multiple drivers have 1. This leads to an illusion that I missed potential drivers.
result1["is_correct_driver_identified"].mean()

0.9226907630522089

In [138]:
result1.sort_values("order_id")

driver_id  participant_status      order_id  driver_gps_accuracy  \
0     719156396976                   1  100131421417                  3.0   
1     395187854079                   1  100366662102                  3.0   
2     147658953745                   1  100692755013                  3.0   
3     559491438109                   0  100734662310                  3.0   
4     175281972887                   1  100824485300                  3.0   
...            ...                 ...           ...                  ...   
3979  219035351732                   1  999257820208                  3.0   
3980  282101591580                   1  999311233908                  3.0   
3981  415077493904                   1  999634594617                  3.0   
3982  606694558181                   0  999929224715                  3.0   
3983  656337628233                   0  999929224715                  3.0   

       customer_id  trip_distance  dayofweek  driver_response_time  \
0     831791436040          3.083          0                 0.584   
1     899256686447          5.315          0                 0.917   
2     925696921521          1.903          0                 0.866   
3     551704487225          3.226          6                15.019   
4     751340700772          5.039          6                 6.588   
...            ...            ...        ...                   ...   
3979  729735748589          4.429          6                 6.961   
3980  336506206293          1.230          0                 0.805   
3981  938180916600          2.127          6                 0.930   
3982  443812741292          3.070          0                15.018   
3983  443812741292          3.070          0                15.023   

      is_busy_hour  driver_distance  driver_cluster_label  \
0                0         0.306670                     5   
1                0         0.226455                     7   
2                1         0.014454                    12   
3                1         0.005282                    14   
4                0         0.161577                    10   
...            ...              ...                   ...   
3979             1         0.388386                    11   
3980             0         0.674789                     3   
3981             1         0.021889                    17   
3982             1         0.344160                    22   
3983             1         0.591712                     3   

      customer_cluster_label  index  Pred_y  is_correct_driver_identified  
0                          9  34975       1                             1  
1                          7  16247       1                             1  
2                         12   2847       1                             1  
3                         14  25749       1                             0  
4                         10   4328       1                             1  
...                      ...    ...     ...                           ...  
3979                      11   6340       1                             1  
3980                       3   9871       1                             1  
3981                      17  17398       1                             1  
3982                       3  28179       1                             0  
3983                       3  31174       0                             0  

[3984 rows x 15 columns]

In [77]:
result1.loc[(result1["order_id"]==526935910500)]

driver_id  participant_status      order_id  driver_gps_accuracy  \
1854  219035351732                   0  526935910500                  3.0   
1855  153978039175                   1  526935910500                  3.0   

       customer_id  trip_distance  dayofweek  driver_response_time  \
1854  785765171897          6.328          6                15.018   
1855  785765171897          6.328          6                 0.817   

      is_busy_hour  driver_distance  driver_cluster_label  \
1854             1         0.224356                    24   
1855             1         0.464020                     1   

      customer_cluster_label  index  Pred_y  
1854                      24   6359       1  
1855                      24   3170       0

In [51]:
result1.sort_values("order_id")

driver_id  participant_status      order_id  driver_gps_accuracy  \
0     719156396976                   1  100131421417                  3.0   
1     395187854079                   1  100366662102                  3.0   
2     147658953745                   1  100692755013                  3.0   
3     559491438109                   0  100734662310                  3.0   
4     175281972887                   1  100824485300                  3.0   
...            ...                 ...           ...                  ...   
3979  219035351732                   1  999257820208                  3.0   
3980  282101591580                   1  999311233908                  3.0   
3981  415077493904                   1  999634594617                  3.0   
3982  606694558181                   0  999929224715                  3.0   
3983  656337628233                   0  999929224715                  3.0   

       customer_id  trip_distance  dayofweek  driver_response_time  \
0     831791436040          3.083          0                 0.584   
1     899256686447          5.315          0                 0.917   
2     925696921521          1.903          0                 0.866   
3     551704487225          3.226          6                15.019   
4     751340700772          5.039          6                 6.588   
...            ...            ...        ...                   ...   
3979  729735748589          4.429          6                 6.961   
3980  336506206293          1.230          0                 0.805   
3981  938180916600          2.127          6                 0.930   
3982  443812741292          3.070          0                15.018   
3983  443812741292          3.070          0                15.023   

      is_busy_hour  driver_distance  driver_cluster_label  \
0                0         0.306670                     5   
1                0         0.226455                     7   
2                1         0.014454                    12   
3                1         0.005282                    14   
4                0         0.161577                    10   
...            ...              ...                   ...   
3979             1         0.388386                    11   
3980             0         0.674789                     3   
3981             1         0.021889                    17   
3982             1         0.344160                    22   
3983             1         0.591712                     3   

      customer_cluster_label  index  Pred_y  
0                          9  34975       1  
1                          7  16247       1  
2                         12   2847       1  
3                         14  25749       1  
4                         10   4328       1  
...                      ...    ...     ...  
3979                      11   6340       1  
3980                       3   9871       1  
3981                      17  17398       1  
3982                       3  28179       1  
3983                       3  31174       0  

[3984 rows x 14 columns]

In [40]:
transformed_test_data_x = transformed_test_data.drop(["order_id","customer_id"],axis=1)
test_pred_y = clf.predict(transformed_test_data_x)
test_pred_y_df = pd.DataFrame(test_pred_y,columns=["Pred_y"])
test_pred_y_df["index"]=test_pred_y_df.index
transformed_test_data["index"] = transformed_test_data.index
x = pd.merge(transformed_test_data,test_pred_y_df,on="index").drop_duplicates()
result2 = pd.DataFrame(x.sort_values("Pred_y",ascending=False).groupby('order_id').first().reset_index())
result2 = result2[["order_id","driver_id"]]

In [41]:
result2.to_csv("results_mahima.csv")

In [42]:
param_grid = { 
    'n_estimators': [200, 500],
    'max_features': ['auto', 'sqrt', 'log2'],
    'max_depth' : [4,8,16,32],
    'criterion' :['entropy','gini'],
}


rf_estimator = RandomForestClassifier(n_jobs=-1,random_state=33,bootstrap=False,class_weight="balanced")
CV_rfc = GridSearchCV(estimator=rf_estimator, param_grid=param_grid, cv= 4)
CV_rfc.fit(train_x,train_y)
CV_rfc.best_params_

KeyboardInterrupt: 

In [ ]:
#dict(zip(features, CV_rfc.best_estimator_.feature_importances_))     
y_true=val_y.values
y_pred=CV_rfc.best_estimator_.predict(val_x.values,type = 'prob')
# y_pred=rf_estimator.predict(df_test[features].values)

In [ ]:
metrics = {}
metrics["f_score_class_1"]=f1_score(y_true,y_pred,pos_label=1)
metrics["f_score_class_0"]=f1_score(y_true,y_pred,pos_label=0)
metrics